In [1]:
import pandas as pd
import csv
from sklearn.ensemble import VotingClassifier
from xgboost import XGBClassifier
from catboost import CatBoostClassifier
from sklearn.ensemble import RandomForestClassifier

In [2]:
df = pd.read_csv('train.csv')

In [3]:
# text_to_find = 'noninvasive'
# columns_to_drop = [col for col in df.columns if text_to_find in col]
# df.drop(columns=columns_to_drop, inplace=True)

In [4]:
df = pd.get_dummies(df)

In [5]:
numeric_columns = df.select_dtypes(include=['int64','float64']).columns
numeric_columns = numeric_columns.drop(['RecordID', 'hospital_id', 'icu_id', 'hospital_death'])

In [6]:
object_columns = df.select_dtypes(include=['object']).columns
object_columns

Index([], dtype='object')

In [7]:
from sklearn.impute import SimpleImputer
import numpy as np

imr = SimpleImputer(missing_values=np.nan, strategy='median')
df[numeric_columns] = imr.fit_transform(df[numeric_columns].values)

In [8]:
from sklearn.preprocessing import RobustScaler


rbs1 = RobustScaler()
df[numeric_columns] = rbs1.fit_transform(df[numeric_columns])

In [9]:
X = df.loc[:, df.columns != 'hospital_death']
y = df[['hospital_death']]

In [10]:
df_test = pd.read_csv('test.csv')
# columns_to_drop = [col for col in df_test.columns if text_to_find in col]
# df_test.drop(columns=columns_to_drop, inplace=True)

df_test = pd.get_dummies(df_test)

imr_test = SimpleImputer(missing_values=np.nan, strategy='median')
df_test[numeric_columns] = imr_test.fit_transform(df_test[numeric_columns].values)

rbs = RobustScaler()
df_test[numeric_columns] = rbs.fit_transform(df_test[numeric_columns])

In [11]:
from lightgbm import LGBMClassifier
from sklearn.ensemble import BaggingClassifier
from sklearn.neighbors import KNeighborsClassifier
from sklearn.pipeline import Pipeline


Bg = BaggingClassifier(base_estimator=XGBClassifier(n_estimators=349,learning_rate=0.1, max_depth=3,subsample = 0.8,min_child_weight=3),n_estimators=100,n_jobs=-1) 
pipeline = Pipeline([('scaler', RobustScaler()), ('xgcl', Bg)])
pipeline.fit(X, y)
md_probs = pipeline.predict_proba(df_test)
md_probs = md_probs[:,1]

bg_1 = BaggingClassifier(CatBoostClassifier(n_estimators=373, learning_rate=0.1,max_depth=3, subsample = 0.8),n_estimators=100,n_jobs=-1)
bg_1.fit(X, y)
md_probs = bg_1.predict_proba(df_test)
md_probs = md_probs[:,1]

bg_2 = BaggingClassifier(RandomForestClassifier(criterion = 'log_loss', max_depth = 11, max_features = 'sqrt', min_samples_leaf = 8, min_samples_split = 5, n_estimators = 400),n_estimators=100,n_jobs=-1)
bg_2.fit(X, y)
md_probs = bg_2.predict_proba(df_test)
md_probs = md_probs[:,1]

scale_knn = Pipeline([("scaler", RobustScaler()), ("knr", KNeighborsClassifier(n_neighbors=651 ,p=1,weights='distance'))])
scale_knn.fit(X, y)
md_probs = scale_knn.predict_proba(df_test)
md_probs = md_probs[:,1]

vc = VotingClassifier(estimators=[('xgBoost', pipeline), ('catBoost', bg_1) , ('RandomForest' ,bg_2), ('KNN',scale_knn)], voting='soft',n_jobs=-1,weights=[2,1,1,1])
vc.fit(X, y)
md_probs = vc.predict_proba(df_test)
md_probs = md_probs[:,1]

filepath = 'out.csv'
with open(filepath, mode='w', newline='') as file: 
    writer = csv.writer(file)
    c=1
    for i in md_probs:
        writer.writerow([50000+c , i])
        c=c+1

/Users/irtiza/Library/Python/3.9/lib/python/site-packages/sklearn/ensemble/_bagging.py:802: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
/Users/irtiza/Library/Python/3.9/lib/python/site-packages/sklearn/ensemble/_base.py:156: FutureWarning: `base_estimator` was renamed to `estimator` in version 1.2 and will be removed in 1.4.
  warnings.warn(
/Users/irtiza/Library/Python/3.9/lib/python/site-packages/sklearn/ensemble/_bagging.py:802: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


0:	learn: 0.5818827	total: 78.3ms	remaining: 29.1s
0:	learn: 0.5844873	total: 78.3ms	remaining: 29.1s
1:	learn: 0.5010243	total: 85.9ms	remaining: 15.9s
1:	learn: 0.4910792	total: 87.9ms	remaining: 16.3s
2:	learn: 0.4334238	total: 93.6ms	remaining: 11.5s
2:	learn: 0.4276113	total: 96.5ms	remaining: 11.9s
3:	learn: 0.3882878	total: 105ms	remaining: 9.69s
0:	learn: 0.5843399	total: 68.7ms	remaining: 25.6s
3:	learn: 0.3837933	total: 113ms	remaining: 10.4s
0:	learn: 0.5835886	total: 70.2ms	remaining: 26.1s
4:	learn: 0.3553118	total: 119ms	remaining: 8.78s
0:	learn: 0.5826596	total: 77.6ms	remaining: 28.9s
0:	learn: 0.5832921	total: 78.6ms	remaining: 29.2s
1:	learn: 0.5014746	total: 85.7ms	remaining: 15.9s
0:	learn: 0.5829724	total: 79.9ms	remaining: 29.7s
0:	learn: 0.5824218	total: 79.3ms	remaining: 29.5s
1:	learn: 0.5001989	total: 82.7ms	remaining: 15.3s
4:	learn: 0.3481538	total: 129ms	remaining: 9.5s
2:	learn: 0.4343585	total: 98ms	remaining: 12.1s
1:	learn: 0.4990639	total: 95.1ms	rema

/Users/irtiza/Library/Python/3.9/lib/python/site-packages/sklearn/ensemble/_bagging.py:802: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
/Users/irtiza/Library/Python/3.9/lib/python/site-packages/sklearn/neighbors/_classification.py:233: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  return self._fit(X, y)
/Users/irtiza/Library/Python/3.9/lib/python/site-packages/sklearn/preprocessing/_label.py:97: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
/Users/irtiza/Library/Python/3.9/lib/python/site-packages/sklearn/preprocessing/_label.py:132: DataConversionWarning: A column-vector y was passed when a 1d

0:	learn: 0.5831054	total: 104ms	remaining: 38.7s
1:	learn: 0.4951645	total: 198ms	remaining: 36.8s
0:	learn: 0.5811598	total: 23.9ms	remaining: 8.88s
2:	learn: 0.4370671	total: 244ms	remaining: 30s
0:	learn: 0.5853561	total: 23.9ms	remaining: 8.9s
3:	learn: 0.3865286	total: 269ms	remaining: 24.9s
1:	learn: 0.4930495	total: 94.5ms	remaining: 17.5s
1:	learn: 0.5029300	total: 85.6ms	remaining: 15.9s
4:	learn: 0.3524941	total: 320ms	remaining: 23.5s
5:	learn: 0.3196987	total: 342ms	remaining: 20.9s
2:	learn: 0.4300803	total: 164ms	remaining: 20.2s
0:	learn: 0.5828082	total: 23.3ms	remaining: 8.67s
2:	learn: 0.4356590	total: 164ms	remaining: 20.2s
3:	learn: 0.3817174	total: 187ms	remaining: 17.2s
0:	learn: 0.5823400	total: 31.6ms	remaining: 11.8s
1:	learn: 0.4979949	total: 48.4ms	remaining: 8.98s
0:	learn: 0.5830628	total: 20.4ms	remaining: 7.59s
3:	learn: 0.3866925	total: 187ms	remaining: 17.2s
0:	learn: 0.5834973	total: 75.9ms	remaining: 28.2s
0:	learn: 0.5823081	total: 58.7ms	remaining:

/Users/irtiza/Library/Python/3.9/lib/python/site-packages/sklearn/ensemble/_base.py:156: FutureWarning: `base_estimator` was renamed to `estimator` in version 1.2 and will be removed in 1.4.
  warnings.warn(


6:	learn: 0.3008340	total: 360ms	remaining: 18.8s
11:	learn: 0.2521129	total: 514ms	remaining: 15.4s
11:	learn: 0.2416719	total: 531ms	remaining: 16s
9:	learn: 0.2580714	total: 381ms	remaining: 13.8s
7:	learn: 0.2831239	total: 441ms	remaining: 20.1s
8:	learn: 0.2692052	total: 458ms	remaining: 18.5s
7:	learn: 0.2864949	total: 493ms	remaining: 22.5s
14:	learn: 0.2331419	total: 870ms	remaining: 20.8s
7:	learn: 0.2843736	total: 498ms	remaining: 22.7s
9:	learn: 0.2602355	total: 504ms	remaining: 18.3s
8:	learn: 0.2713801	total: 496ms	remaining: 20.1s
8:	learn: 0.2714399	total: 550ms	remaining: 22.3s
12:	learn: 0.2471040	total: 677ms	remaining: 18.7s
12:	learn: 0.2373531	total: 698ms	remaining: 19.3s
10:	learn: 0.2482686	total: 558ms	remaining: 18.4s
8:	learn: 0.2688082	total: 556ms	remaining: 22.5s
9:	learn: 0.2626092	total: 547ms	remaining: 19.9s
15:	learn: 0.2297533	total: 949ms	remaining: 21.2s
10:	learn: 0.2499205	total: 577ms	remaining: 19s
13:	learn: 0.2419585	total: 734ms	remaining: 1